In [121]:
from pymongo import MongoClient
import pandas as pd
import numpy as np
import json
import requests
client = MongoClient("localhost:27017")
client.list_database_names()

['Aliens', 'Ironhack', 'admin', 'config', 'local']

In [111]:
mydb = client['Aliens']
mydb.list_collection_names()

['airports']

In [95]:
print(mydb)

Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'Aliens')


In [112]:
collection = client.get_database("Aliens")
collection

Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'Aliens')

In [97]:
collection = db["airports"]

In [101]:
collection.create_index([("type_point_", "2dsphere")])

'type_point__2dsphere'

In [98]:
print(collection)

Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'Aliens'), 'airports')


In [107]:
airports = pd.read_csv("F_usairports.csv")
airports.shape
airports.head()

type                                name  latitude_deg  \
0       heliport                   Total Rf Heliport     40.070801   
1  small_airport                Aero B Ranch Airport     38.704022   
2  small_airport                        Lowell Field     59.947733   
3  small_airport                        Epps Airpark     34.864799   
4         closed  Newport Hospital & Clinic Heliport     35.608700   

   longitude_deg  elevation_ft iso_country  
0     -74.933601          11.0          US  
1    -101.473911        3435.0          US  
2    -151.692524         450.0          US  
3     -86.770302         820.0          US  
4     -91.254898         237.0          US

In [108]:
airportsdict = airports.to_dict(orient='records')

In [113]:
#airportsdict

In [109]:
collection.insert_many(airportsdict)

# Insertar Sucesos

In [114]:
collection2 = db["aliens"]

In [115]:
collection2.create_index([("type_point_", "2dsphere")])

'type_point__2dsphere'

In [116]:
print(collection2)

Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'Aliens'), 'aliens')


In [117]:
cases = pd.read_csv("F_usacases.csv")

In [118]:
casesdict = cases.to_dict(orient='records')

In [119]:
collection2.insert_many(casesdict)

# GEOQUERIES

In [120]:
# distancia desde el avistamiento
metros = 300

In [ ]:
coord = type_point()
coord

In [ ]:
query = {"location": {"$near": {"$geometry": coord, "$maxDistance": metros}}}

## 2 Análisis

- 1 Distancia del evento a aeropuertos
- 2 Distancia del aeropuerto a distintos eventos

Sacar una nueva columna en el dataframe donde se vea la distancia al aeropuerto mas cercano
Otra columna con el nombre de ese aeropuerto

Value counts de la columna aeropuertos con más eventos asociados. (Cómo se relaciona la distancia y cuales son los aeropuertos más "activos")

# GEOPANDAS

In [61]:
pip install geopandas

  Using cached geopandas-0.10.2-py2.py3-none-any.whl (1.0 MB)
  Using cached Fiona-1.8.20-cp38-cp38-manylinux_2_5_x86_64.manylinux1_x86_64.whl (15.4 MB)
  Using cached Shapely-1.8.0-cp38-cp38-manylinux_2_5_x86_64.manylinux1_x86_64.whl (1.1 MB)
     |████████████████████████████████| 5.8 MB 446 kB/s eta 0:00:01    |▋                               | 102 kB 699 kB/s eta 0:00:09     |█▎                              | 235 kB 699 kB/s eta 0:00:09     |██▋                             | 471 kB 699 kB/s eta 0:00:08     |██████████▉                     | 2.0 MB 616 kB/s eta 0:00:07     |██████████████████▊             | 3.4 MB 867 kB/s eta 0:00:03     |███████████████████████▉        | 4.4 MB 716 kB/s eta 0:00:03
  Using cached cligj-0.7.2-py3-none-any.whl (7.1 kB)
  Using cached munch-2.5.0-py2.py3-none-any.whl (10 kB)
  Using cached click_plugins-1.1.1-py2.py3-none-any.whl (7.5 kB)
Note: you may need to restart the kernel to use updated packages.


In [62]:
import geopandas as gpd

In [63]:
type(airports)

pandas.core.frame.DataFrame

In [64]:
airports.head(1)

type               name  latitude_deg  longitude_deg  elevation_ft  \
0  heliport  Total Rf Heliport     40.070801     -74.933601          11.0   

  iso_country  
0          US

In [66]:
gdf = gpd.GeoDataFrame(airports, geometry=gpd.points_from_xy(airports.longitude_deg, airports.latitude_deg))

In [67]:
gdf.sample()

type                            name  latitude_deg  longitude_deg  \
5230  heliport  Metropolitan Electric Heliport     40.887299     -74.163803   

      elevation_ft iso_country                    geometry  
5230         220.0          US  POINT (-74.16380 40.88730)

In [68]:
type(gdf)

geopandas.geodataframe.GeoDataFrame

In [70]:
pip install cartoframes

  Using cached cartoframes-1.2.4-py2.py3-none-any.whl (245 kB)
  Using cached semantic_version-2.8.5-py2.py3-none-any.whl (15 kB)
  Using cached Unidecode-1.3.2-py3-none-any.whl (235 kB)
  Using cached carto-1.11.3-py3-none-any.whl
  Using cached pyrestcli-0.6.11-py3-none-any.whl
Note: you may need to restart the kernel to use updated packages.


In [71]:
from cartoframes.viz import Map, Layer, popup_element

In [72]:
Map(Layer(gdf, "color:purple", popup_hover=[popup_element("type", "Airports US")]))

In [73]:
bases = pd.read_csv("F_usabases.csv")

In [74]:
bases.sample()

Base   Latitude  Longitude
442  TURKEY  37.881168   41.13509

In [76]:
gdfbases = gpd.GeoDataFrame(bases, geometry=gpd.points_from_xy(bases.Longitude, bases.Latitude))

In [79]:
Map(Layer(gdfbases, "color:green", popup_hover=[popup_element("Base", "Bases US")]))

In [80]:
cases = pd.read_csv("F_usacases.csv")

In [81]:
cases.sample()

datetime     city state country  shape duration (seconds)  \
49395  2011-07-30  dubuque    ia      us  light                600   

      duration (hours/min)                                           comments  \
49395       about 10 mins?  Single bright&#44 moving winking light and &#8...   

      date posted   latitude  longitude  
49395    8/7/2011  42.500556 -90.664444

In [82]:
gdfcases = gpd.GeoDataFrame(cases, geometry=gpd.points_from_xy(cases.longitude, cases.latitude))

In [90]:
gdfcases = gdfcases.dropna()

In [92]:
Map(Layer(gdfcases,"color:blue", popup_hover=[popup_element("comments", "Casos")]),encode_data=False,)